### Theoretical Part

##### Hypothesis Testing: the problem of multiple comparisons 

Given that:
- $\alpha$ is the Type I error for each test
- $\beta$ is the Type II error
- $1 - \beta$ is the power

a) P($m^{th}$ experiment gives significant result | $m$ experiments lacking power to reject $H_0$) = $\alpha (1 - \beta)^{m-1}$,

where $(1 - \beta)^{m-1}$ is the probability that the first $m - 1$ experiments correctly conclude that the result is not significant, and $\alpha$ is the probability that the next experiment will yield a Type I error. We can rephrase this event as
> Experiment 1 correctly rejects $H_0$ **AND** Experiment 2 correctly rejects $H_0$ **AND ... AND** Experiment $m$ yields a Type I error.

b) P(at least one significant result | $m$ experiments lacking power to reject $H_0$) = $m \alpha$. 

We can rephrase this event as 
> Experiment 1 yields a Type I error **OR** Experiment 2 yields a Type I error **OR ... OR** Experiment $m$ yields a Type I error.

which can be translated into an $m$-fold addition of the Type I error probability $\alpha$.

##### Bias and unfairness in Interleaving experiments

We present a situation where interleaving should produce a preference for one of the two ranking lists but 
it fails to do so and it assigns equal expected winning probability to both rankings.

Let $d_3$ be the only relevant document, i.e. the only document the user will click on.
In list A, $d_3$ is ranked as third, whereas $d_3$ is in the second position of Ranking A. Therefore, Ranking B is expected to win more often than Ranking B. Consider, however, the following rankings and the four lists that can be generated using Team Draft Interleaving:

In [ ]:
from IPython.display import Image
Image("interleaving_bias.png")

In [ ]:
# Step 1: Simulate Rankings of Relevance for E and P

import itertools

relevance = [0, 1, 2]  # 0: N, 1: R, 2: HR
combinations = list(itertools.product(relevance, repeat=5))
ranking_pairs = list(itertools.product(combinations, repeat=2))

# delete ratings that are the same for both  
for i,k in enumerate(ranking_pairs):
    if k[0] == k[1]:
        del ranking_pairs[i]
k = 10
for pair in ranking_pairs[:k]:
    print(pair)
    
    

In [ ]:
def average_precision(query_judgement):
    l = []
    rel_docs = 0
    
    for i, judgement in enumerate(query_judgement, start=1):
        if judgement != 0:
            rel_docs += 1
            l.append(rel_docs / i)
            
    if rel_docs == 0:
        return 0
    
    return sum(l) / rel_docs       

In [ ]:
from math import log

def dcg(query_judgement, k):
    query_judgement = list(query_judgement)[:k]
    dcg = 0
    
    for i, judgement in enumerate(query_judgement, start=1):
        dcg += (2 ** judgement - 1) / log(i + 1, 2)
        
    return dcg

def ndcg(query_judgement, k):
    perfect_ordering = sorted(query_judgement, reverse=True)
    perfect_score = dcg(perfect_ordering, k)
    
    if perfect_score == 0:
        return 0
    
    return dcg(query_judgement, k) / perfect_score

In [ ]:
max_rel = 2  # ad-hoc for 3 different judgements
satisfaction_probs = [(2 ** rel - 1) / 2 ** max_rel for rel in range(3)]

def err(query_judgement):
    sat_probs = []
    
    for rel in query_judgement:
        sat_probs.append(satisfaction_probs[rel])
        
    err = 0
    
    for i in range(1, len(query_judgement) + 1):
        prod = sat_probs[i - 1]
        
        for j in range(1, i):
            prod *= 1 - sat_probs[j]
        
        err += prod / i
    
#     if err == 0:
#         return len(query_judgement)
    
    return err

In [ ]:
max_rel = 2  # ad-hoc for 3 different judgements
satisfaction_probs = [(2 ** rel - 1) / 2 ** max_rel for rel in range(3)]

def err(query_judgement):
    sat_probs = []
    
    for rel in query_judgement:
        sat_probs.append(satisfaction_probs[rel])
        
    err = 0
    prod = 1
    
    for i in range(1, len(query_judgement) + 1):
        rel_prob = sat_probs[i - 1]
        
        err += prod * rel_prob / i
        prod *= 1 - rel_prob
            
#     if err == 0:
#         return len(query_judgement)
    
    return err

In [ ]:
print(1/ err(ranking_pairs[11][1]))

In [ ]:
ranking_pairs[242][1]

In [13]:
import random
import copy


def team_draft_interleaving(list_a, list_b):
    '''
    Implementation of the team draft interleaving algorithm
    Args:
        a, b: list
    Return:
        interleaved_list, chosen_list
    '''
    final_list = []
    chosen = []  # list containing a/b values

    # This is done so that, original lists are not modified
    a = copy.deepcopy(list_a)
    b = copy.deepcopy(list_b)
    
    while (len(a) > 0 and len(b) > 0):
        choose_a = bool(random.getrandbits(1))

        label_add = ['a', 'b']

        current_a = a.pop(0)
        current_b = b.pop(0)

        to_add = list(set([current_a, current_b]))

        if not choose_a:
            to_add = to_add[::-1]  # reverse list
            label_add = label_add[::-1]

        # TODO: Check if t
        if len(to_add) == 1:
            del label_add[1]
            
        final_list += to_add
        chosen += label_add

        if current_b in a: a.remove(current_b)
        if current_a in b: b.remove(current_a)

    return final_list, chosen

In [ ]:
def simulate_clicks(doc_size, num_clicks=2):
    return random.sample(range(doc_size), num_clicks)

In [ ]:
def team_draft_credit(pointer_list, simulated_clicks):
    
    credit_a, credit_b = 0, 0
    
    for idx in simulated_clicks:
        credit_a += pointer_list[idx] == 'a'
        credit_b += pointer_list[idx] == 'b'
    
    return credit_a, credit_b

In [ ]:
a = [1, 2, 3, 4]
b = [2, 3, 4, 1]

interleaved, pointers = team_draft_interleaving(a, b)
clicks = simulate_clicks(len(a), 2)

print('-'*51)
print('interleaved     :', interleaved)
print('pointers     :', pointers)
print('clicks       :', [interleaved[c] for c in clicks], ' {NOTE: these are docIDs}')
print('credit (a, b):', team_draft_credit(pointers, clicks))
print('-'*51)

In [2]:
## click models

# data:  SessionID, TimePassed, TypeOfAction, QueryID, RegionID, ListOfURLs

data = []
with open("YandexRelPredChallenge.txt","r") as yandex:
    
    for line in yandex:
        data.append(line.strip().split('\t'))
        print(line.strip().split('\t'))


['0', '0', 'Q', '8', '0', '7', '103', '51', '92', '43', '12', '73', '69', '27', '105']
['0', '36', 'Q', '174', '0', '1625', '1627', '1623', '1626', '1624', '1622', '1619', '1621', '1620', '1618']
['0', '50', 'Q', '227', '0', '2094', '2091', '2087', '2089', '2093', '2088', '2090', '2092', '2095', '2086']
['0', '515', 'Q', '174', '0', '1625', '1627', '1623', '1626', '1624', '1622', '1619', '1621', '1620', '1618']
['0', '524', 'Q', '1974', '0', '17562', '1627', '1626', '1623', '2091', '17559', '17563', '17558', '17561', '17560']
['0', '527', 'C', '17562']
['0', '528', 'C', '1627']
['0', '529', 'C', '1626']
['1', '0', 'Q', '9', '0', '13', '70', '66', '94', '50', '104', '29', '21', '89', '85']
['1', '20', 'C', '104']
['1', '123', 'C', '21']
['1', '291', 'Q', '1324', '0', '11807', '11805', '11812', '11813', '11804', '11809', '11806', '11811', '11808', '11810']
['1', '301', 'C', '11813']
['1', '8605', 'C', '11808']
['1', '8737', 'C', '11810']
['1', '8884', 'C', '11811']
['2', '0', 'Q', '7', '

['163', '22841', 'C', '408308']
['163', '23561', 'Q', '52054', '0', '415045', '415043', '415047', '415039', '415040', '415041', '415038', '415046', '415044', '415042']
['163', '23724', 'Q', '40669', '0', '327465', '45740', '24560', '12047', '24611', '327463', '327464', '16543', '327462', '327466']
['163', '23727', 'C', '45740']
['163', '23940', 'Q', '32', '0', '314', '230', '338', '282', '335', '257', '216', '241', '342', '281']
['163', '23945', 'C', '314']
['163', '26863', 'Q', '54813', '0', '436199', '436202', '436198', '436195', '436203', '436200', '436196', '387275', '436201', '436197']
['163', '26911', 'Q', '54851', '0', '436199', '436517', '436512', '436510', '436516', '436515', '436511', '436514', '436518', '436513']
['163', '26938', 'C', '387275']
['163', '31046', 'Q', '57744', '0', '458502', '458501', '458499', '458503', '458498', '458505', '458504', '458496', '458497', '458500']
['163', '31049', 'C', '458502']
['163', '31063', 'Q', '57744', '0', '458502', '458501', '458499', 

['400', '1428', 'Q', '5444', '0', '46966', '46960', '46962', '46959', '46965', '46963', '46961', '43259', '46964', '46958']
['400', '1443', 'C', '46966']
['400', '2021', 'Q', '7366', '0', '63032', '63033', '63035', '63028', '63031', '6277', '63029', '63034', '63027', '63030']
['400', '2032', 'C', '63032']
['400', '2321', 'C', '63033']
['400', '2445', 'Q', '9156', '0', '77771', '77770', '77769', '77767', '77774', '77772', '77775', '77768', '77773', '77766']
['400', '2470', 'C', '77770']
['400', '2532', 'C', '77769']
['401', '0', 'Q', '323', '0', '2920', '2896', '2952', '2919', '2934', '2897', '2889', '2936', '2887', '2881']
['401', '2834', 'Q', '9892', '0', '83804', '83805', '83800', '83803', '83796', '83798', '83813', '83802', '83812', '83810']
['401', '2845', 'C', '83804']
['401', '2902', 'C', '83800']
['401', '2942', 'Q', '10345', '0', '83803', '83800', '83796', '83804', '83805', '87422', '83802', '83813', '83810', '87430']
['402', '0', 'Q', '321', '1', '2938', '2954', '2958', '2955'

['658', '747', 'Q', '62', '0', '505', '649', '661', '613', '646', '640', '672', '354', '638', '4641']
['658', '767', 'C', '646']
['658', '879', 'Q', '62', '0', '505', '649', '661', '613', '646', '640', '672', '354', '638', '4641']
['658', '1108', 'C', '646']
['658', '1986', 'Q', '7704', '0', '65840', '65842', '65841', '65838', '17220', '64959', '65839', '65835', '65837', '65836']
['658', '3277', 'Q', '62', '0', '505', '649', '661', '613', '646', '640', '672', '354', '638', '4641']
['658', '3285', 'C', '613']
['658', '3315', 'C', '646']
['659', '0', 'Q', '232', '0', '355', '364', '2114', '365', '45', '2133', '366', '400', '383', '1368']
['659', '5', 'C', '355']
['659', '1209', 'Q', '4838', '0', '41978', '41973', '41967', '41975', '41971', '41970', '41977', '41969', '41976', '41966']
['659', '1895', 'C', '41978']
['659', '1932', 'C', '41975']
['659', '2079', 'C', '41976']
['660', '0', 'Q', '527', '0', '4698', '4718', '4704', '4748', '4735', '4750', '4714', '4699', '4746', '4693']
['660',

['945', '1907', 'Q', '7584', '0', '64872', '57100', '64870', '64871', '64875', '64874', '64878', '64876', '64877', '64873']
['945', '1986', 'Q', '7829', '0', '64872', '64871', '64878', '66931', '66936', '66932', '66935', '64874', '66933', '66934']
['945', '2070', 'Q', '8131', '0', '64872', '69393', '66932', '64871', '64878', '69391', '66936', '69392', '69394', '66935']
['945', '2197', 'Q', '8131', '0', '64872', '69393', '66932', '64871', '64878', '69391', '66936', '69392', '69394', '66935']
['945', '2283', 'Q', '8795', '0', '74899', '74902', '74900', '74896', '74901', '74894', '74893', '74895', '74898', '74897']
['945', '2357', 'Q', '9042', '0', '4728', '76835', '76833', '76831', '76837', '76834', '76836', '76830', '76832', '76829']
['945', '2460', 'Q', '9375', '0', '79592', '79584', '79585', '79589', '79591', '79586', '79583', '79588', '79590', '79587']
['945', '3016', 'Q', '11163', '0', '94060', '94065', '94067', '94059', '94063', '94064', '94062', '94061', '94066', '94058']
['945', 

...

['12412', '1311', 'Q', '17654', '0', '146290', '146288', '146291', '135804', '146286', '146283', '146284', '146287', '146285', '146289']
['12412', '1321', 'C', '146288']
['12412', '1535', 'C', '146291']
['12412', '1771', 'C', '146286']
['12413', '0', 'Q', '1763', '0', '15673', '15655', '15661', '15669', '15680', '15663', '15671', '15652', '15666', '15662']
['12413', '5', 'C', '15673']
['12415', '0', 'Q', '32', '0', '314', '230', '338', '282', '335', '257', '216', '241', '342', '281']
['12415', '11', 'C', '314']
['12416', '0', 'Q', '253', '1', '2356', '2275', '2372', '2291', '2333', '2373', '2310', '2317', '2273', '2258']
['12416', '22', 'C', '2372']
['12416', '66', 'C', '2291']
['12416', '261', 'C', '2273']
['12416', '1275', 'C', '2273']
['12417', '0', 'Q', '13399', '1', '112075', '112074', '112073', '112067', '112068', '112070', '112066', '112072', '112069', '112071']
['12417', '117', 'Q', '13768', '1', '112074', '115123', '115125', '112072', '115118', '115126', '115124', '115121', '1

['12721', '4037', 'C', '208411']
['12721', '4063', 'Q', '32', '0', '314', '230', '338', '282', '335', '257', '216', '241', '342', '281']
['12721', '4064', 'C', '314']
['12721', '7263', 'Q', '13918', '0', '45', '11749', '116318', '58144', '20', '7552', '11779', '11743', '42683', '115412']
['12721', '7266', 'C', '11749']
['12721', '9253', 'Q', '37327', '0', '301653', '301651', '301649', '301647', '301650', '301648', '301652', '301654', '301655', '301656']
['12722', '0', 'Q', '573', '0', '5143', '5162', '5178', '5190', '5145', '5153', '5173', '5174', '5151', '5148']
['12722', '13', 'C', '5145']
['12722', '130', 'C', '5162']
['12723', '0', 'Q', '3482', '1', '759', '24121', '30494', '30483', '30507', '30501', '30498', '30487', '2490', '30480']
['12723', '56', 'C', '759']
['12724', '0', 'Q', '13806', '0', '115416', '115420', '115411', '115414', '115419', '115415', '115410', '115417', '115418', '115413']
['12724', '5', 'C', '115416']
['12724', '47', 'C', '115411']
['12724', '70', 'C', '115419

['13052', '309', 'Q', '902', '1', '290', '977', '360', '421', '917', '2284', '345', '397', '2368', '1426']
['13052', '320', 'C', '290']
['13052', '335', 'C', '360']
['13052', '340', 'C', '421']
['13052', '426', 'C', '917']
['13052', '468', 'C', '345']
['13052', '473', 'C', '397']
['13052', '478', 'C', '2368']
['13052', '1529', 'Q', '19276', '1', '159148', '159152', '159150', '159147', '159149', '159153', '159151', '159146', '159145', '159144']
['13052', '1544', 'C', '159153']
['13052', '1599', 'Q', '19512', '1', '160971', '160976', '160972', '160977', '160969', '160970', '160975', '160973', '160974', '24705']
['13052', '1673', 'Q', '19752', '1', '160976', '160971', '160977', '162917', '24705', '160970', '162919', '160973', '162921', '162918']
['13052', '1704', 'Q', '19752', '1', '160976', '160971', '160977', '160970', '162918', '163744', '163743', '163745', '163747', '163746']
['13052', '2282', 'Q', '21493', '1', '176580', '176586', '176585', '176577', '176592', '176595', '176596', '17

['13370', '10', 'C', '2935']
['13370', '61', 'C', '2908']
['13372', '0', 'Q', '649', '0', '5836', '425', '5839', '5854', '566', '5866', '5868', '5832', '5828', '5871']
['13372', '11', 'C', '5836']
['13373', '0', 'Q', '6', '3', '46', '419', '10', '49', '123726', '14', '106', '28', '123724', '123725']
['13373', '6', 'C', '46']
['13373', '130', 'C', '46']
['13373', '315', 'C', '46']
['13374', '0', 'Q', '143', '0', '355', '1409', '45', '364', '366', '1328', '1368', '1320', '365', '379']
['13374', '11', 'C', '355']
['13375', '0', 'Q', '297', '0', '438', '451', '2693', '2692', '1860', '4923', '434', '4903', '4933', '2746']
['13375', '108', 'C', '438']
['13375', '4885', 'C', '438']
['13375', '20902', 'C', '438']
['13375', '20941', 'C', '438']
['13376', '0', 'Q', '4892', '1', '42389', '42396', '42369', '42366', '42393', '42392', '123784', '123783', '123786', '123785']
['13376', '3', 'C', '42389']
['13376', '1831', 'Q', '1138', '1', '3043', '10192', '10168', '2988', '10190', '10139', '10180', '

['13706', '3031', 'C', '138149']
['13707', '0', 'Q', '590', '0', '5382', '5323', '5378', '5370', '5375', '5332', '5361', '5347', '5315', '5359']
['13707', '95', 'C', '5382']
['13707', '129', 'C', '5359']
['13707', '2231', 'Q', '6299', '0', '39460', '54081', '13163', '54080', '39457', '54079', '39456', '54083', '39461', '54082']
['13707', '2297', 'C', '39457']
['13707', '2300', 'C', '39460']
['13707', '2538', 'C', '54081']
['13708', '0', 'Q', '4414', '0', '38314', '38318', '38306', '38312', '38321', '38316', '38304', '38311', '38320', '38309']
['13708', '20', 'C', '38306']
['13709', '0', 'Q', '143', '0', '355', '1409', '45', '364', '366', '1328', '1368', '1320', '365', '379']
['13709', '5', 'C', '355']
['13711', '0', 'Q', '1778', '1', '15830', '15800', '15841', '15836', '15833', '15815', '15829', '15846', '15805', '15820']
['13711', '38', 'Q', '1123', '1', '1536', '1550', '1555', '1607', '11942', '1590', '1567', '49810', '128948', '1544']
['13711', '72', 'C', '1555']
['13715', '0', 'Q',

In [ ]:
# Random click model: param and prediction

from numpy import random
import numpy as np


def rcm_param(data):
    clicks = 0
    number_docs_shown = 0
    for line in data:
        if line[2] == "C":
            clicks += 1
        
        if line[2] == "Q":
            number_docs_shown += len(line[5:])
        
    return clicks / number_docs_shown

def rcm_predict(ranked_list, p):
    clicks = []
    for u in ranked_list:
        click = np.random.binomial(1, p)
        if click:
            clicks.append(u)
    return clicks
            
        
        

In [ ]:
print(rcm_predict(range(10), rcm_param(data)))

## Simplified Dynamic Bayesian Network Model

In [85]:
def DBN(ranked_list, 
        query, 
        attractiveness, 
        satisfaction, 
        examination, 
        continuation):
    '''
    Implementation of the Simplified Dynamic Bayesian Network model
    Args:
        ranked_list: an ascendingly ordered list of document IDs
        attractiveness: a dict of attractiveness parameters
        satisfaction: a dict of satisfaction parameters
        examination: a list of examination parameters
        continuation: the continuation parameter
    Return:
        list of clicked document IDs
    '''
    
    q = query
    clicks = []
    
    for r, u in enumerate(ranked_list):
        click_prob = attractiveness[(u, q)] * examination[r]
        
        # Click with probability alpha_uq * epsilon_r
        if np.random.binomial(1, click_prob):
            clicks.append(u)
            
            # Satisfied with probability sigma_uq
            if np.random.binomial(1, satisfaction[(u, q)]):
                break
                
            # If not satisfied, continue with probability lambda
            if np.random.binomial(1, 1 - continuation):
                break

    return clicks
        

In [86]:
from collections import defaultdict, OrderedDict

class Session:
    '''
    A Session object stores the queries submitted during that
    session, the documents presented for each query, and the 
    user clicks (paired with the rank of the clicked document
    according to the retrieved document list). Session objects
    also carry an index.
    '''
    def __init__(self, index):
        self.id = index
        
        # queryID -> list of returned docIDs
        self.query_to_docs = OrderedDict()
        
        # queryID -> list of (click, rank) tuples
        # Each click is paired with the rank of the clicked 
        # document according to the retrieved document list.
        self.query_to_click_rank = OrderedDict()
        
        
    def add_query(self, query, doc_list):
        '''
        Args:
            query: a queryID
            doc_list: an ascendingly ordered list of docIDs
        '''
        if query in self.query_to_docs.keys():
            
            if self.query_to_docs[query] == doc_list:
                self.query_to_docs.move_to_end(query)
            else:
                del self.query_to_docs[query]
                self.query_to_docs[query] = doc_list
                
        else:
            self.query_to_docs[query] = doc_list
        
        
    def add_click(self, query, doc, rank):
        '''
        Args:
            query: a queryID
            doc: a docID
            rank: the rank of the clicked document
        '''
        try:
            self.query_to_click_rank[query].append((doc, rank))
        except KeyError:
            self.query_to_click_rank[query] = [(doc, rank)]
    
    
    def docs_till_last_clicked(self):
        '''
        Returns a dict containing, for each query q, only the first L docIDs, 
        where L is the rank of the last clicked document for q.
        '''
        query_to_first_l_docs = OrderedDict()
        
        for query, doc_list in self.query_to_docs.items():
            try:
                # get the rank of the last clicked document
                last_doc, rank = self.query_to_click_rank[query][-1]
            except KeyError:
                # if there have been no clicks for this query, 
                # use the length of the retrieved document list
                rank = len(doc_list)
            
            query_to_first_l_docs[query] = doc_list[:rank]
        
        return query_to_first_l_docs
    
    
    def last_clicked(self):
        '''
        Returns a list of the last clicked document (IDs)
        for all queries in this session.
        '''
        last_clicked = []
        
        for q in self.query_to_click_rank.keys():
            try:
                doc, _ = self.query_to_click_rank[q][-1]
                last_clicked.append(doc)
            except IndexError:
                pass  # no clicks for this query
        
        return last_clicked
        

In [87]:
def read_sessions(filepath):
    '''
    Reads YandexRelPredChallenge and returns a list of all Session 
    objects corresponding to the search sessions in the file.
    '''
    sessions = []
    
    with open(filepath, 'r') as log:
        sess = Session(0)  # create first Session
        for line in log:
            line = line.strip().split('\t')
            
            # new session has started
            if int(line[0]) != sess.id:
                # append last session to return list
                sessions.append(copy.deepcopy(sess))
                # create new Session
                sess = Session(int(line[0]))
            
            # Queries
            if line[2] == 'Q':
                queryID = int(line[3])
                doc_list = list(map(int, line[5:]))
                sess.add_query(queryID, doc_list)
            
            # Clicks
            if line[2] == 'C':
                last_query = list(sess.query_to_docs.keys())[-1]
                try:
                    docID = int(line[3])
                    rank = sess.query_to_docs[last_query].index(docID) + 1
                    sess.add_click(last_query, docID, rank)
                except ValueError:
                    pass  # clicked doc is not in the list of proposed docs !?
#                     print(line[3], sess.query_to_docs[last_query])
    
    return sessions
                

In [88]:
# A modest test
sessions = read_sessions("YandexRelPredChallenge.txt")

for s in sessions[:2]:
    for q in s.query_to_docs.keys():
        print(q, s.query_to_docs[q])
    print()
    print(s.query_to_click_rank)
    print()

8 [7, 103, 51, 92, 43, 12, 73, 69, 27, 105]
227 [2094, 2091, 2087, 2089, 2093, 2088, 2090, 2092, 2095, 2086]
174 [1625, 1627, 1623, 1626, 1624, 1622, 1619, 1621, 1620, 1618]
1974 [17562, 1627, 1626, 1623, 2091, 17559, 17563, 17558, 17561, 17560]

OrderedDict([(1974, [(17562, 1), (1627, 2), (1626, 3)])])

9 [13, 70, 66, 94, 50, 104, 29, 21, 89, 85]
1324 [11807, 11805, 11812, 11813, 11804, 11809, 11806, 11811, 11808, 11810]

OrderedDict([(9, [(104, 6), (21, 8)]), (1324, [(11813, 4), (11808, 9), (11810, 10), (11811, 8)])])



In [89]:
def estimate_SDBN_params(sessions):
    
    # (doc, query) -> the number of sessions where doc is 
    # presented for query above or at the last-clicked rank
    S = defaultdict(int) 
    # (doc, query) -> the number of sessions where a click on doc occurred
    S_prime = defaultdict(int)

    alpha = defaultdict(int)  # attractiveness parameters
    sigma = defaultdict(int)  # satisfaction parameters
    epsilon = [1]  # examination parameters  (examination prob of the first doc is 1)
    
    for sess in sessions:
        for query, docs in sess.docs_till_last_clicked().items():
            for doc in docs:
                # doc is presented at least at the last clicked rank in this session
                S[(doc, query)] += 1 
        
        for query in sess.query_to_click_rank.keys():
            click_rank_pairs = sess.query_to_click_rank[query]
            
            tabu = []
            for doc, rank in click_rank_pairs:
                # a click on doc from query occurred in this session: count this click 
                # only if it was not already counted for this doc-query pair *in this session*
                if (doc, query) not in tabu:
                    S_prime[(doc, query)] += 1
                    tabu.append((doc, query))
                
                alpha[(doc, query)] += 1
                
                if doc in sess.last_clicked():
                    # count 1 when doc is the last clicked document for query
                    sigma[(doc, query)] += 1
        
        # Normalise
        # TODO: what to do with the zero values in S?
        for doc, query in alpha.keys():
            try:
                alpha[(doc, query)] /= S[(doc, query)]
            except ZeroDivisionError:
                alpha[(doc, query)] = 0
            
            sigma[(doc, query)] /= S_prime[(doc, query)]
            
    return alpha, sigma, epsilon  # TODO: epsilon !?

In [90]:
# yandex_sessions = read_sessions("YandexRelPredChallenge.txt")
alpha, sigma, epsilon = estimate_SDBN_params(sessions[:2])

# print(len(alpha), len(sigma), len(epsilon))
print(alpha)
print(sigma)


defaultdict(<class 'int'>, {(17562, 1974): 1.0, (1627, 1974): 1.0, (1626, 1974): 1.0, (104, 9): 1.0, (21, 9): 1.0, (11813, 1324): 1.0, (11808, 1324): 0, (11810, 1324): 0, (11811, 1324): 1.0})
defaultdict(<class 'int'>, {(1626, 1974): 1.0, (17562, 1974): 0.0, (1627, 1974): 0.0, (21, 9): 1.0, (11811, 1324): 1.0, (104, 9): 0.0, (11813, 1324): 0.0, (11808, 1324): 0.0, (11810, 1324): 0.0})
